In [2]:
from sqlalchemy import create_engine
import pandas as pd
import numpy as np
import os

Setup database connection

In [2]:
DATABASE_TYPE = 'postgresql'
DBAPI = 'psycopg2'
HOST = '127.0.0.1'  
USER = 'postgres'
PASSWORD = 'password'
DATABASE = 'PM25'
PORT = 5432  


engine = create_engine(f"{DATABASE_TYPE}+{DBAPI}://{USER}:{PASSWORD}@{HOST}:{PORT}/{DATABASE}")

Load cleaned table aqi_cleaned into DF

In [3]:

sql_file_path = os.path.join("..", "..", "02_SQL_queries", "03_data_transformation","26_aqi_cleaned_ALL.sql")


with open(sql_file_path, 'r') as file:
    query = file.read()

df = pd.read_sql(query, engine)


print(df.head())       
print(df.info())       


         date country         city variable  count   min   max  median  \
0  2023-02-03      US  Little Rock      dew     36  -7.0  -1.0    -4.0   
1  2023-02-17      US  Little Rock      dew     42  -8.0  -3.0    -6.0   
2  2023-02-28      US  Little Rock      dew     40   3.0   7.0     4.0   
3  2023-03-11      US  Little Rock      dew     36   3.0  10.0     8.0   
4  2023-03-18      US  Little Rock      dew     48 -11.0  -2.0    -8.0   

   variance  
0     35.43  
1     23.32  
2     18.46  
3     55.52  
4     99.57  
<class 'pandas.core.frame.DataFrame'>
RangeIndex: 6729716 entries, 0 to 6729715
Data columns (total 9 columns):
 #   Column    Dtype  
---  ------    -----  
 0   date      object 
 1   country   object 
 2   city      object 
 3   variable  object 
 4   count     int64  
 5   min       float64
 6   max       float64
 7   median    float64
 8   variance  float64
dtypes: float64(4), int64(1), object(4)
memory usage: 462.1+ MB
None


To make interpolation easier DF is broken down into smaller files sorted by variable, interpolated, and recombined before entering them back into the DB

In [4]:
unique_variables = df['variable'].unique()

# Create an empty dictionary to store DataFrames for each variable
variable_dfs = {}

# Loop through each unique variable
for var in unique_variables:
    # Filter the DataFrame for rows where the 'variable' column matches the current variable
    variable_dfs[var] = df[df['variable'] == var]


In [5]:
# Check that keys match all variables in dataset
variable_dfs.keys()

dict_keys(['dew', 'temperature', 'humidity', 'o3', 'pm25', 'pressure', 'wind-speed', 'pm10', 'so2', 'no2', 'wind-gust', 'co', 'wd', 'precipitation', 'uvi'])

In [6]:
# Check the shape of each DataFrame in the dictionary against db to verify all information sorted correctly
for var, df_var in variable_dfs.items():
    print(f"DataFrame for {var} has {df_var.shape[0]} rows and {df_var.shape[1]} columns")


DataFrame for dew has 452247 rows and 9 columns
DataFrame for temperature has 637273 rows and 9 columns
DataFrame for humidity has 635089 rows and 9 columns
DataFrame for o3 has 615277 rows and 9 columns
DataFrame for pm25 has 643049 rows and 9 columns
DataFrame for pressure has 637028 rows and 9 columns
DataFrame for wind-speed has 607471 rows and 9 columns
DataFrame for pm10 has 623546 rows and 9 columns
DataFrame for so2 has 421457 rows and 9 columns
DataFrame for no2 has 651821 rows and 9 columns
DataFrame for wind-gust has 362819 rows and 9 columns
DataFrame for co has 373553 rows and 9 columns
DataFrame for wd has 49251 rows and 9 columns
DataFrame for precipitation has 14045 rows and 9 columns
DataFrame for uvi has 5790 rows and 9 columns


In [7]:
# Save each variable CSV into directory for backup
for k, i in variable_dfs.items():
    
    file_path = os.path.join("..", "..", "01_data", "03_generated_from_python", "interpolation", "variable_CSV", f"{k}.csv")
    variable_dfs[k].to_csv(file_path)
    print(f"Saved CSV {k}")
    

Saved CSV dew
Saved CSV temperature
Saved CSV humidity
Saved CSV o3
Saved CSV pm25
Saved CSV pressure
Saved CSV wind-speed
Saved CSV pm10
Saved CSV so2
Saved CSV no2
Saved CSV wind-gust
Saved CSV co
Saved CSV wd
Saved CSV precipitation
Saved CSV uvi


Missing dates will be inserted into the df so that each city/variable will have the full range of rows by date for the time period weather there is data or not. These placeholders will allow interpolated data to be inserted. First an idndex of the entire date range is created.  It is then inserted into the each df grouped by city.  

In [8]:
# Get the min and max dates across all DataFrames
min_date = min(df['date'].min() for df in variable_dfs.values())
max_date = max(df['date'].max() for df in variable_dfs.values())

print(f"Min Date: {min_date}")
print(f"Max Date: {max_date}")


Min Date: 2018-01-01
Max Date: 2023-12-31


In [9]:
# Create a date index for the complete range
date_index = pd.date_range(start=min_date, end=max_date, freq='D')

print(f"Date Index: {date_index}")


Date Index: DatetimeIndex(['2018-01-01', '2018-01-02', '2018-01-03', '2018-01-04',
               '2018-01-05', '2018-01-06', '2018-01-07', '2018-01-08',
               '2018-01-09', '2018-01-10',
               ...
               '2023-12-22', '2023-12-23', '2023-12-24', '2023-12-25',
               '2023-12-26', '2023-12-27', '2023-12-28', '2023-12-29',
               '2023-12-30', '2023-12-31'],
              dtype='datetime64[ns]', length=2191, freq='D')


A list of dates from each city grouping is then matched against the full index and its difference becomes the dates that need to be inserted into the DF.  New rows are inserted keeping the country/city/variable columns and NaN values for the rest.  The files are saved as new CSVs for redundency before being interpolated.

In [ ]:
# Loop through the variable dataframes
for var, df_var in variable_dfs.items():
    # Group by 'city' to process each city individually
    df_var_grouped = df_var.groupby('city')

    # List to collect the updated dataframes
    updated_dfs = []

    for city, group in df_var_grouped:
        # Get a list of dates that already exist in the current city's dataframe
        existing_dates = group['date'].unique()

        # Find the missing dates by checking the full date range
        missing_dates = date_index.difference(existing_dates)

        # Grab the values for other columns (e.g., 'country', 'variable') directly by column name
        country = group['country'].iloc[0]  # using .iloc[0] because all rows are the same
        variable = group['variable'].iloc[0]
        
        # Create new rows for missing dates with NaN for the columns that will be interpolated ; keep the 'country', 'city', and 'variable' columns intact
        missing_rows = pd.DataFrame({
            'date': missing_dates,
            'country': country,
            'city': city,
            'variable': variable,
            'count' : "9999", # denote an obvios number so that interpolated data is easily identified
            'min' : np.nan, # fill in NaN for rest of columns
            'max' : np.nan,
            'median' : np.nan,
            'variance' : np.nan
              
        })

        # Append the missing rows to the existing data for the city
        group = pd.concat([group, missing_rows])
        group['date'] = pd.to_datetime(group['date'])

        # Ensure the dataframe is sorted by 'date'
        group = group.sort_values(by='date')

       

        # Add the updated dataframe for this city to the list
        updated_dfs.append(group)

        # Concatenate all the updated city dataframes together
    updated_df = pd.concat(updated_dfs)

    # Store the updated dataframe back in the dictionary for redundency
    #variable_dfs[var] = updated_df

    # Save the updated dataframe to CSV
    updated_df.to_csv(os.path.join("..","..","01_data","03_generated_from_python","interpolation","missing_dates_CSV",f"missing_{var}.csv"), index=False)

    print(f"Updated DataFrame for {var} has been saved.")


Updated DataFrame for dew has been saved.
Updated DataFrame for temperature has been saved.
Updated DataFrame for humidity has been saved.
Updated DataFrame for o3 has been saved.
Updated DataFrame for pm25 has been saved.
Updated DataFrame for pressure has been saved.
Updated DataFrame for wind-speed has been saved.
Updated DataFrame for pm10 has been saved.
Updated DataFrame for so2 has been saved.
Updated DataFrame for no2 has been saved.
Updated DataFrame for wind-gust has been saved.
Updated DataFrame for co has been saved.
Updated DataFrame for wd has been saved.
Updated DataFrame for precipitation has been saved.
Updated DataFrame for uvi has been saved.


A linear interpolation method is used to fill in missing data as it is the most simple and efficient method while maintaining continuity amidst short gaps (8days or less)

In [17]:
path = os.path.join("..","..","01_data","03_generated_from_python","interpolation","missing_dates_CSV")
savepath = os.path.join("..","..","01_data","03_generated_from_python","interpolation","interpolated_CSV")


def interpolate_fill(series):
    series = series.interpolate(method='linear', limit_direction='both')
    series = series.fillna(method='ffill').fillna(method='bfill')
    return series.round(2).astype(float)

for filename in os.listdir(path):
    if filename.endswith('.csv'):  # Only process CSV files
        file_path = os.path.join(path, filename)
        df = pd.read_csv(file_path)
        df['date'] = pd.to_datetime(df['date'])
        df = df.sort_values(by=['country', 'city', 'date'])
        #grouped = df.groupby(['country', 'city'])


        # Group and apply interpolation with transform
        df['min'] = df.groupby(['country', 'city'])['min'].transform(interpolate_fill)
        df['max'] = df.groupby(['country', 'city'])['max'].transform(interpolate_fill)
        df['median'] = df.groupby(['country', 'city'])['median'].transform(interpolate_fill)
        df['variance'] = df.groupby(['country', 'city'])['variance'].transform(interpolate_fill)
        df['sd'] = df.groupby(['country', 'city'])['sd'].transform(interpolate_fill)

        save_file_path = os.path.join(savepath,"INT_" + filename)
        
        # Save the updated DataFrame
        df.to_csv(save_file_path, index=False)

        print(f"Processed and saved: {save_file_path}")


C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series

Processed and saved: ..\..\01_data\03_generated_from_python\interpolation\interpolated_CSV\_INTmissing_co.csv


C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series

Processed and saved: ..\..\01_data\03_generated_from_python\interpolation\interpolated_CSV\_INTmissing_dew.csv


C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series

...

Processed and saved: ..\..\01_data\03_generated_from_python\interpolation\interpolated_CSV\_INTmissing_wd.csv


C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series

Processed and saved: ..\..\01_data\03_generated_from_python\interpolation\interpolated_CSV\_INTmissing_wind-gust.csv


C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series = series.fillna(method='ffill').fillna(method='bfill')
C:\Users\13476\AppData\Local\Temp\ipykernel_20800\3463810644.py:7: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  series

Processed and saved: ..\..\01_data\03_generated_from_python\interpolation\interpolated_CSV\_INTmissing_wind-speed.csv


The interpolated files are then looped over and interpolated data over 8 consecutive days is dropped

In [ ]:
path = os.path.join("..","..","01_data","03_generated_from_python","interpolation","interpolated_CSV")
save_path = os.path.join("..","..","01_data","03_generated_from_python","interpolation","cleaned_CSV")

for filename in os.listdir(path):

    if filename.endswith('.csv'):  # Only process CSV files

        file_path = os.path.join(path, filename)
        df = pd.read_csv(file_path)

        # Create a boolean mask where 'count' is 9999
        mask_9999 = df['count'] == 9999

        # Track consecutive 9999s by shifting the mask and comparing
        consecutive_9999 = mask_9999 & mask_9999.shift(fill_value=False)

        # Use `cumsum` to group the consecutive 9999s together
        consecutive_groups = consecutive_9999.cumsum()

        # Initialize a counter for consecutive 9999 values
        count_9999 = 0

        # Iterate over the rows where the value is 9999 and count consecutive occurrences
        for i in range(len(df)):
            if mask_9999[i]:
                count_9999 += 1  # Increment for consecutive 9999
                if count_9999 > 8:
                    # Set 'min', 'max', 'median', 'variance', and 'sd' columns to 0
                    df.loc[i, ['min', 'max', 'median', 'variance']] = 0
            else:
                count_9999 = 0  # Reset counter when value is not 9999

        # Save the result to a new CSV file
        df.to_csv(os.path.join(save_path,f"CLEAN_INT_{filename}"), index=False)    

           

            



clean CSVs to ensure no trailing commas

In [ ]:
path = os.path.join("..","..","01_data","03_generated_from_python","interpolation","cleaned_CSV")

# Iterate through all files in the directory
for file in os.listdir(path):
    if file.endswith(".csv"):
        input_file = os.path.join(path, file)
        output_file = os.path.join(path, f"cleaned_{file}")
        
        # Open the file, clean trailing commas, and save
        with open(input_file, 'r') as infile, open(output_file, 'w') as outfile:
            for line in infile:
                # Remove trailing commas and write to a new file
                outfile.write(line.rstrip(',') + '\n')

print("Cleaning complete. Cleaned files saved with 'cleaned_' prefix.")


Cleaning complete. Cleaned files saved with 'cleaned_' prefix.


Combine CSVs back into one

In [14]:

path = input("Enter the path to the directory containing the CSV files: ").strip()

# Remove surrounding quotes if present
if path.startswith('"') and path.endswith('"'):
    path = path[1:-1]

# Replace single backslashes with double backslashes for Windows compatibility
path = path.replace('\\', '\\\\')

file_type = input("Enter the file type (e.g., 'csv'): ").strip().lower()
filter_string = input("Enter a string to filter filenames (leave blank for all files): ").strip()

try:
    # List all files in the directory that match the specified file type
    csv_files = [
        f for f in os.listdir(path) 
        if f.endswith(f'.{file_type}') and (filter_string in f if filter_string else True)
    ]

    # Check if any files were found
    if not csv_files:
        print("No files found matching the criteria.")
    else:
        # Use a list comprehension to read and store DataFrames
        df_list = [pd.read_csv(os.path.join(path, file)) for file in csv_files]

        # Concatenate all DataFrames
        combined_df = pd.concat(df_list, ignore_index=True)

        # Get the name for the output file based on the first file's name and the filter string
        base_name = csv_files[0][:5]  # First 5 characters of the first file name
        filter_part = f'_{filter_string}' if filter_string else ''
        output_file_name = f'{base_name}{filter_part}_COMB.csv'

        # Save the combined DataFrame to a new CSV file in the specified directory
        combined_df.to_csv(os.path.join(path, output_file_name), index=False)

        print("Done!")

except Exception as e:
    print(f"Error: {e}")



Done!
